In [295]:
import os
import pandas as pd
from tqdm import tqdm

import warnings
warnings.simplefilter(action='ignore', category=pd.errors.DtypeWarning)

In [296]:
# CSV with the finished Globocan dataset
GLOBOCAN_input = input().strip()

  C:\Users\svalb\OneDrive\Escritorio\Data_40_years_cancer_studies\resources\Globocan_dataset_ready.csv


In [297]:
# Directory to save Globocan dataset with required columns only
GLOBOCAN_prepared_output = input().strip()

  C:\Users\svalb\OneDrive\Escritorio\Data_40_years_cancer_studies\resources\


In [298]:
# Directory with the csvs of the articles' dataset with country and cancer names matching those of GLOBOCAN dataset
DF_input = input().strip()

  C:\Users\svalb\OneDrive\Escritorio\Data_40_years_cancer_studies\parsedXMLs_match_GLOBOCAN\


In [299]:
# Directory to save aggregated articles' datasets
DF_prepared_output = input().strip()

   C:\Users\svalb\OneDrive\Escritorio\Data_40_years_cancer_studies\resources\


## Part 1 - Preparing Globocan dataset
Right now, the Globocan dataset has a number of columns which are not required for preparing the visualizations:

In [300]:
df_globocan = pd.read_csv(GLOBOCAN_input)
df_globocan.columns.to_list()

['Alpha-3 code',
 'Cancer code',
 'Population code (ISO/UN)',
 'Country',
 'Sex',
 'Number',
 '95% UI low',
 '95% UI high',
 'Number.1',
 'ASR (World)',
 'Crude rate',
 'Cumulative risk',
 'Cancer']

### 1.1.- Remove unnecessary columns  
Only the columns **Country**, **Cancer**, **ASR (World)** and **Crude rate** are important in this project. ASR (World) refers to the age-standardized rate, whereas Crude rate refers to the raw (non age-standardized) rate.  Here, a new csv is saved with only these columns.

In [301]:
df_globocan_lite = df_globocan[["Country",  "Cancer", "ASR (World)", "Crude rate"]]
df_globocan_lite

Country                 Cancer  ASR (World)  Crude rate
0                  Afghanistan            Anal cancer         0.47        0.27
1                      Albania            Anal cancer         0.24        0.38
2                      Algeria            Anal cancer         0.34        0.35
3                       Angola            Anal cancer         0.24        0.11
4                   Azerbaijan            Anal cancer         0.87        1.00
5                    Argentina            Anal cancer         0.50        0.64
6                    Australia            Anal cancer         1.40        2.50
7                      Austria            Anal cancer         1.10        2.20
8                      Bahamas            Anal cancer         1.30        1.50
9                      Bahrain            Anal cancer         0.24        0.17
10                  Bangladesh            Anal cancer         0.24        0.22
11                     Armenia            Anal cancer         0.24        0.40
12                    Barbados            Anal cancer         1.40        2.80
13                     Belgium            Anal cancer         1.00        2.10
14                      Bhutan            Anal cancer         0.00        0.00
15                     Bolivia            Anal cancer         0.08        0.08
16      Bosnia and Herzegovina            Anal cancer         0.16        0.31
17                    Botswana            Anal cancer         0.71        0.66
18                      Brazil            Anal cancer         1.10        1.50
19                      Belize            Anal cancer         0.00        0.00
20             Solomon Islands            Anal cancer         0.35        0.28
21           Brunei Darussalam            Anal cancer         0.00        0.00
22                    Bulgaria            Anal cancer         0.49        0.99
23                     Myanmar            Anal cancer         0.31        0.32
24                     Burundi            Anal cancer         0.99        0.43
25                     Belarus            Anal cancer         0.75        1.40
26                    Cambodia            Anal cancer         0.29        0.24
27                    Cameroon            Anal cancer         0.68        0.37
28                      Canada            Anal cancer         1.20        2.30
29                  Cabo Verde            Anal cancer         0.39        0.35
30    Central African Republic            Anal cancer         0.57        0.32
31                   Sri Lanka            Anal cancer         0.41        0.64
32                        Chad            Anal cancer         0.13        0.05
33                       Chile            Anal cancer         0.38        0.61
34                       China            Anal cancer         0.22        0.39
35                    Colombia            Anal cancer         0.78        1.00
36                     Comoros            Anal cancer         0.00        0.00
37              Congo Republic            Anal cancer         0.84        0.50
38                    DR Congo            Anal cancer         0.98        0.52
39                  Costa Rica            Anal cancer         0.23        0.35
40                     Croatia            Anal cancer         0.48        1.10
41                        Cuba            Anal cancer         0.83        1.60
42                      Cyprus            Anal cancer         0.51        0.90
43                     Czechia            Anal cancer         1.10        2.50
44                       Benin            Anal cancer         0.65        0.38
45                     Denmark            Anal cancer         1.60        3.10
46          Dominican Republic            Anal cancer         0.16        0.18
47                     Ecuador            Anal cancer         0.66        0.73
48                 El Salvador            Anal cancer         0.25        0.29
49                    Ethiopia            Anal cancer         0.44       

In [302]:
df_globocan_lite.to_csv(GLOBOCAN_prepared_output + "Globocan_dataset_ready_lite.csv", index = False)

### 1.2.- Cummulative cancer incidence (all cancers) per country
Even though the dataset contains both the ASR and the crude incidence values (see above), in principle only the ASR values will be displayed. Here, a new dataset is created containing the sum of the cancer incidences (ASR) of all cancers per country

In [63]:
df_globocan_cumm_ASR_country = df_globocan_lite[["Country", "ASR (World)"]].groupby(by=["Country"]).sum()

In [64]:
df_globocan_cumm_ASR_country

ASR (World)
Country                 
Afghanistan       126.09
Albania           212.70
Algeria           195.96
Angola            179.38
Argentina         305.01
...                  ...
Venezuela         264.73
Vietnam           188.78
Yemen             100.07
Zambia            236.40
Zimbabwe          298.15

[185 rows x 1 columns]

In [65]:
df_globocan_cumm_ASR_country.to_csv(GLOBOCAN_prepared_output + "Globocan_dataset_cummulative_ASR_country.csv", index = False)

### 1.3.- Cancer with highest incidence per country
A new dataset will be saved containing the name of the cancer with highest incidence (ASR) per country

In [70]:
highest_incidence_idx = df_globocan_lite.groupby(by="Country")["ASR (World)"].idxmax()
df_globocan_max_ASR_country = df_globocan_lite.iloc[highest_incidence_idx]
df_globocan_max_ASR_country

Country             Cancer  ASR (World)  Crude rate
555                Afghanistan      Breast cancer         29.4        17.9
556                    Albania      Breast cancer         51.1        72.6
557                    Algeria      Breast cancer         61.9        65.1
4258                    Angola    Prostate cancer         47.9        15.1
560                  Argentina      Breast cancer         71.3        91.8
566                    Armenia      Breast cancer         39.6        64.4
6111                 Australia        Skin cancer        177.1       297.7
562                    Austria      Breast cancer         69.5       130.3
559                 Azerbaijan      Breast cancer         32.9        42.6
4263                   Bahamas    Prostate cancer         89.1       102.2
564                    Bahrain      Breast cancer         58.5        51.7
3525                Bangladesh  Esophageal cancer         16.0        15.0
4267                  Barbados    Prostate cancer        100.5       188.4
4280                   Belarus    Prostate cancer         68.2       113.1
568                    Belgium      Breast cancer        104.4       191.5
574                     Belize      Breast cancer         46.8        41.0
4299                     Benin    Prostate cancer         38.0        16.4
4824                    Bhutan     Stomach cancer         15.9        14.6
755                    Bolivia    Cervical cancer         38.7        37.0
571     Bosnia and Herzegovina      Breast cancer         51.9        92.8
757                   Botswana    Cervical cancer         39.1        36.1
4273                    Brazil    Prostate cancer         76.3        97.0
576          Brunei Darussalam      Breast cancer         50.2        61.1
577                   Bulgaria      Breast cancer         52.8       101.0
4432              Burkina Faso    Prostate cancer         35.3        10.4
764                    Burundi    Cervical cancer         43.6        22.9
4284                Cabo Verde    Prostate cancer         43.6        27.0
581                   Cambodia      Breast cancer         25.1        24.1
582                   Cameroon      Breast cancer         48.6        30.2
583                     Canada      Breast cancer         88.6       164.7
585   Central African Republic      Breast cancer         37.7        22.7
4287                      Chad    Prostate cancer         82.2        29.7
4288                     Chile    Prostate cancer         62.3       101.9
5399                     China        Lung cancer         40.8        75.1
4290                  Colombia    Prostate cancer         52.6        65.2
776                    Comoros    Cervical cancer         52.0        36.3
4292            Congo Republic    Prostate cancer         42.3        15.2
4294                Costa Rica    Prostate cancer         45.6        69.4
4336             Cote d'Ivoire    Prostate cancer         63.8        28.9
595                    Croatia      Breast cancer         74.6       148.0
4296                      Cuba    Prostate cancer         58.1       119.4
597                     Cyprus      Breast cancer        104.8       166.7
598                    Czechia      Breast cancer         72.5       142.0
4293                  DR Congo    Prostate cancer         40.1        16.4
600                    Denmark      Breast cancer         95.4       179.2
612                   Djibouti      Breast cancer         38.1        37.2
4301        Dominican Republic    Prostate cancer         86.1        89.1
602                    Ecuador      Breast cancer         39.5        43.1
728                      Egypt      Breast cancer         55.4        51.1
4303               El Salvador    Prostate cancer         41.9        45.5
605                    Eritrea      Breast cancer         37.8        27.5
4306                   Estonia    Prostate cancer         98.8       186.9
898                   Eswatini    Cervical cance

In [71]:
df_globocan_max_ASR_country.to_csv(GLOBOCAN_prepared_output + "Globocan_dataset_max_ASR_country.csv", index = False)

## Part 2 - Calculating aggregated data for articles' dataset
To prepare data in the articles' dataset, aggregates of studies will be calculated grouping by country, cancer type and year.  
Future iterations of the project will deal with animal species as well.

### 2.1.- Aggregate number of articles per year irrespective of country and cancer type 
Here, a csv is prepared aggregating papers by year (i.e. the final csv will have a row per year)

In [303]:
# Import list of csvs to parse
list_csvs_match_GLOBOCAN = []

for file in os.listdir(DF_input):
    if file[-4:] == ".csv":
        list_csvs_match_GLOBOCAN.append(file)

n_csvs_match_GLOBOCAN = len(list_csvs_match_GLOBOCAN)

In [21]:
year_aggregates = {}
for csv in tqdm(list_csvs_match_GLOBOCAN):
    df = pd.read_csv(DF_input + csv)
    dict_agg = df["PublicationDate"].value_counts().to_dict()
    for year in dict_agg.keys():
        if int(year) in year_aggregates.keys():
            year_aggregates[int(year)] += dict_agg[int(year)]
        else:
            year_aggregates[int(year)] = dict_agg[int(year)]
    del df, dict_agg

100%|█████████████████████████| 45/45 [02:33<00:00,  3.41s/it]


In [22]:
year_aggregates

{1992: 53303,
 1991: 51473,
 1990: 53232,
 2001: 72691,
 2002: 76353,
 2000: 71170,
 1999: 66895,
 1998: 64720,
 1995: 58541,
 1997: 62860,
 1996: 61090,
 1994: 58000,
 1993: 55099,
 1989: 51838,
 1988: 47953,
 1986: 42957,
 1987: 44938,
 1985: 41699,
 1984: 16274,
 2003: 81219,
 2004: 85433,
 2005: 91004,
 2006: 94266,
 2007: 99610,
 2013: 147002,
 2008: 104591,
 2016: 175374,
 2009: 109345,
 2010: 117318,
 2011: 125587,
 2012: 138543,
 2015: 170983,
 2019: 201285,
 2014: 161508,
 2017: 180199,
 2018: 187679,
 2021: 249023,
 2020: 226078,
 2022: 245243,
 2023: 237455,
 2025: 3119,
 2024: 160906}

In [44]:
# Convert to pd dataframe
df_year_agg = pd.DataFrame.from_dict(year_aggregates, orient="index", columns = ["Articles"])
df_year_agg.reset_index(inplace=True)
df_year_agg.rename(columns={"index": "Year"}, inplace=True)
df_year_agg.sort_values(by=["Year"], ascending= True, inplace=True)

In [45]:
df_year_agg

Year  Articles
18  1984     16274
17  1985     41699
15  1986     42957
16  1987     44938
14  1988     47953
13  1989     51838
2   1990     53232
1   1991     51473
0   1992     53303
12  1993     55099
11  1994     58000
8   1995     58541
10  1996     61090
9   1997     62860
7   1998     64720
6   1999     66895
5   2000     71170
3   2001     72691
4   2002     76353
19  2003     81219
20  2004     85433
21  2005     91004
22  2006     94266
23  2007     99610
25  2008    104591
27  2009    109345
28  2010    117318
29  2011    125587
30  2012    138543
24  2013    147002
33  2014    161508
31  2015    170983
26  2016    175374
34  2017    180199
35  2018    187679
32  2019    201285
37  2020    226078
36  2021    249023
38  2022    245243
39  2023    237455
41  2024    160906
40  2025      3119

In [46]:
# Save
df_year_agg.to_csv(DF_prepared_output + "articles_year.csv", index=False)

### 2.2.- Aggregate number of articles per country and year irrespective of cancer type
Here, a csv is prepared aggregating papers by year and country (i.e. the final csv will have a row per year and country)

In [87]:
year_country_aggregates = {}

for csv in tqdm(list_csvs_match_GLOBOCAN):
    df = pd.read_csv(DF_input + csv)
    dict_agg = df[["Country", "PublicationDate"]].value_counts().to_dict()
    for key in dict_agg.keys():
        if key[0] in year_country_aggregates.keys() and int(key[1]) in year_country_aggregates[key[0]].keys():
            year_country_aggregates[key[0]][int(key[1])] += dict_agg[(key[0], key[1])]
        elif key[0] in year_country_aggregates.keys():
            year_country_aggregates[key[0]][int(key[1])] = dict_agg[(key[0], key[1])]
        else:
            year_country_aggregates[key[0]] = {}
            year_country_aggregates[key[0]][int(key[1])] = dict_agg[(key[0], key[1])]

year_country_aggregates

100%|█████████████████████████| 45/45 [02:36<00:00,  3.49s/it]


{'United States': {1992: 16637,
  1991: 15154,
  1990: 12177,
  2001: 22427,
  2002: 23274,
  2000: 21889,
  1999: 20441,
  1998: 19568,
  1996: 19355,
  1995: 18769,
  1994: 17439,
  1997: 19672,
  1993: 17162,
  1986: 213,
  1989: 10323,
  2003: 24865,
  2004: 26513,
  2005: 27424,
  1988: 9775,
  2006: 27844,
  2007: 29339,
  1985: 114,
  2008: 30589,
  2016: 45401,
  1987: 4219,
  2009: 31174,
  2010: 32845,
  2011: 34473,
  1984: 27,
  2012: 36613,
  2013: 38079,
  2014: 41358,
  2015: 43941,
  2017: 46776,
  2018: 48405,
  2019: 49761,
  2021: 56565,
  2022: 52964,
  2020: 53664,
  2025: 981,
  2023: 52591,
  2024: 34263},
 'Japan': {1992: 5806,
  1991: 5398,
  1990: 4957,
  2001: 8114,
  2002: 7892,
  2000: 8257,
  1999: 7535,
  1998: 7560,
  1993: 6041,
  1994: 6192,
  1995: 6375,
  1997: 6756,
  1996: 6633,
  1989: 3879,
  2003: 7946,
  2004: 7960,
  2005: 7997,
  1987: 1433,
  2006: 7454,
  2007: 7735,
  2008: 7443,
  1986: 48,
  2009: 7604,
  2010: 7911,
  2011: 8599,
  2012

In [94]:
# Create df from dict
dfs_year_country = []
for country in year_country_aggregates.keys():
    df = pd.DataFrame.from_dict(year_country_aggregates[country], orient="index", columns = ["Articles"])
    df.reset_index(inplace=True)
    df.rename(columns={"index": "Year"}, inplace=True)
    df.sort_values(by=["Year"], ascending= True, inplace=True)
    df["Country"] = country
    dfs_year_country.append(df)

df_year_country_agg = pd.concat(dfs_year_country)

In [95]:
df_year_country_agg

Year  Articles                   Country
28  1984        27             United States
21  1985       114             United States
13  1986       213             United States
24  1987      4219             United States
18  1988      9775             United States
14  1989     10323             United States
2   1990     12177             United States
1   1991     15154             United States
0   1992     16637             United States
12  1993     17162             United States
10  1994     17439             United States
9   1995     18769             United States
8   1996     19355             United States
11  1997     19672             United States
7   1998     19568             United States
6   1999     20441             United States
5   2000     21889             United States
3   2001     22427             United States
4   2002     23274             United States
15  2003     24865             United States
16  2004     26513             United States
17  2005     27424             United States
19  2006     27844             United States
20  2007     29339             United States
22  2008     30589             United States
25  2009     31174             United States
26  2010     32845             United States
27  2011     34473             United States
29  2012     36613             United States
30  2013     38079             United States
31  2014     41358             United States
32  2015     43941             United States
23  2016     45401             United States
33  2017     46776             United States
34  2018     48405             United States
35  2019     49761             United States
38  2020     53664             United States
36  2021     56565             United States
37  2022     52964             United States
40  2023     52591             United States
41  2024     34263             United States
39  2025       981             United States
29  1985         9                     Japan
21  1986        48                     Japan
17  1987      1433                     Japan
28  1988      3319                     Japan
13  1989      3879                     Japan
2   1990      4957                     Japan
1   1991      5398                     Japan
0   1992      5806                     Japan
8   1993      6041                     Japan
9   1994      6192                     Japan
10  1995      6375                     Japan
12  1996      6633                     Japan
11  1997      6756                     Japan
7   1998      7560                     Japan
6   1999      7535                     Japan
5   2000      8257                     Japan
3   2001      8114                     Japan
4   2002      7892                     Japan
14  2003      7946                     Japan
15  2004      7960                     Japan
16  2005      7997                     Japan
18  2006      7454                     Japan
19  2007      7735                     Japan
20  2008      7443                     Japan
22  2009      7604                     Japan
23  2010      7911                     Japan
24  2011      8599                     Japan
25  2012      9489                     Japan
26  2013      8932                     Japan
27  2014      9395                     Japan
31  2015      9455                     Japan
30  2016      9856                     Japan
32  2017     10814                     Japan
33  2018     11265                     Japan
34  2019     11556                     Japan
35  2020     12858                     Japan
37  2021     14538                     Japan
36  2022     13544                     Japan
38  2023     12689                     Japan
39  2024      8314                     Japan
40  2025       140                     Japan
22  1984         4            United Kingdom
23  1985        21            United Kingdom
17  1986        55            United Kingdom
21  1987      1045            United Kingdom
24  1988      1675            United Kingdom

In [96]:
# Save
df_year_country_agg.to_csv(DF_prepared_output + "articles_year_country.csv", index=False)

### 2.3.- Aggregate number of articles per cancer type and year irrespective of country
Here, a csv is prepared aggregating papers by year and cancer type (i.e. the final csv will have a row per year and cancer type). Cancers names are hardcoded from a previous notebook in this project.

In [304]:
cancer_names = [
 'Anal cancer',
 'Bladder cancer',
 'Brain cancer',
 'Breast cancer',
 'Cervical cancer',
 'Colon cancer',
 'Colorectal cancer',
 'Esophageal cancer',
 'Gallbladder cancer',
 'Hodgkin lymphoma',
 'Kaposi sarcoma',
 'Kidney cancer',
 'Laryngeal cancer',
 'Leukemia',
 'Liver cancer',
 'Lung cancer',
 'Mesothelioma',
 'Mouth cancer',
 'Multiple myeloma',
 'Non-Hodgkin lymphoma',
 'Other cancer',
 'Ovarian cancer',
 'Pancreatic cancer',
 'Penile cancer',
 'Prostate cancer',
 'Rectal cancer',
 'Salivary gland cancer',
 'Skin cancer',
 'Stomach cancer',
 'Testicular cancer',
 'Throat cancer',
 'Thyroid cancer',
 'Undetermined_Cancer',
 'Uterine cancer',
 'Vaginal cancer',
 'Vulvar cancer'
]

In [286]:
# Create and structure dict to hold data about publications on each cancer type
year_cancer_aggregates = {}

for cancer in cancer_names:
    year_cancer_aggregates[cancer] = {}

# Parse all articles' csv and count the number of studies per cancer and country
for csv in tqdm(list_csvs_match_GLOBOCAN):
    df = pd.read_csv(DF_input + csv)
    for row in df.index:
        for cancer in cancer_names:
            year = df.at[row, "PublicationDate"]
            if pd.notna(year) and df.at[row, cancer] > 0:
                if int(year) in year_cancer_aggregates[cancer].keys():
                    year_cancer_aggregates[cancer][int(year)] += 1
                else:
                    year_cancer_aggregates[cancer][int(year)] = 1

    del df, cancer, year, csv

year_cancer_aggregates

100%|█████████████████████████| 45/45 [23:56<00:00, 31.92s/it]


{'Anal cancer': {1992: 12,
  1991: 14,
  1990: 14,
  2001: 25,
  1996: 18,
  1999: 18,
  2002: 25,
  1998: 20,
  2003: 32,
  2000: 20,
  2004: 40,
  2005: 40,
  2007: 44,
  2006: 38,
  2008: 68,
  2009: 93,
  2010: 101,
  2011: 104,
  2012: 111,
  1989: 18,
  2013: 145,
  2014: 120,
  2015: 163,
  2016: 163,
  2017: 178,
  2018: 186,
  2025: 4,
  1987: 7,
  1988: 8,
  1986: 3,
  2019: 167,
  2020: 206,
  2021: 196,
  2022: 194,
  2023: 193,
  1984: 1,
  2024: 144,
  1995: 13,
  1993: 15,
  1994: 17,
  1997: 19},
 'Bladder cancer': {1992: 472,
  1991: 384,
  1990: 406,
  2001: 588,
  2000: 611,
  1998: 487,
  1999: 518,
  2002: 605,
  2003: 629,
  1997: 497,
  1996: 531,
  1995: 453,
  2004: 702,
  2005: 731,
  2006: 827,
  1989: 355,
  2007: 881,
  2008: 907,
  1985: 278,
  1993: 427,
  1986: 250,
  1994: 470,
  2009: 947,
  2010: 1054,
  2011: 1136,
  2012: 1324,
  1987: 305,
  2013: 1525,
  2014: 1720,
  1988: 315,
  2015: 1725,
  2016: 1852,
  2017: 1810,
  2018: 2074,
  2020: 2481,

In [288]:
# Create df from dict
dfs_year_cancer = []
for cancer in year_cancer_aggregates.keys():
    df = pd.DataFrame.from_dict(year_cancer_aggregates[cancer], orient="index", columns = ["Articles"])
    df.reset_index(inplace=True)
    df.rename(columns={"index": "Year"}, inplace=True)
    df.sort_values(by=["Year"], ascending= True, inplace=True)
    df["Cancer"] = cancer
    dfs_year_cancer.append(df)

df_year_cancer_agg = pd.concat(dfs_year_cancer)

In [289]:
df_year_cancer_agg

Year  Articles                 Cancer
35  1984         1            Anal cancer
29  1986         3            Anal cancer
27  1987         7            Anal cancer
28  1988         8            Anal cancer
19  1989        18            Anal cancer
2   1990        14            Anal cancer
1   1991        14            Anal cancer
0   1992        12            Anal cancer
38  1993        15            Anal cancer
39  1994        17            Anal cancer
37  1995        13            Anal cancer
4   1996        18            Anal cancer
40  1997        19            Anal cancer
7   1998        20            Anal cancer
5   1999        18            Anal cancer
9   2000        20            Anal cancer
3   2001        25            Anal cancer
6   2002        25            Anal cancer
8   2003        32            Anal cancer
10  2004        40            Anal cancer
11  2005        40            Anal cancer
13  2006        38            Anal cancer
12  2007        44            Anal cancer
14  2008        68            Anal cancer
15  2009        93            Anal cancer
16  2010       101            Anal cancer
17  2011       104            Anal cancer
18  2012       111            Anal cancer
20  2013       145            Anal cancer
21  2014       120            Anal cancer
22  2015       163            Anal cancer
23  2016       163            Anal cancer
24  2017       178            Anal cancer
25  2018       186            Anal cancer
30  2019       167            Anal cancer
31  2020       206            Anal cancer
32  2021       196            Anal cancer
33  2022       194            Anal cancer
34  2023       193            Anal cancer
36  2024       144            Anal cancer
26  2025         4            Anal cancer
40  1984       107         Bladder cancer
18  1985       278         Bladder cancer
20  1986       250         Bladder cancer
26  1987       305         Bladder cancer
29  1988       315         Bladder cancer
15  1989       355         Bladder cancer
2   1990       406         Bladder cancer
1   1991       384         Bladder cancer
0   1992       472         Bladder cancer
19  1993       427         Bladder cancer
21  1994       470         Bladder cancer
11  1995       453         Bladder cancer
10  1996       531         Bladder cancer
9   1997       497         Bladder cancer
5   1998       487         Bladder cancer
6   1999       518         Bladder cancer
4   2000       611         Bladder cancer
3   2001       588         Bladder cancer
7   2002       605         Bladder cancer
8   2003       629         Bladder cancer
12  2004       702         Bladder cancer
13  2005       731         Bladder cancer
14  2006       827         Bladder cancer
16  2007       881         Bladder cancer
17  2008       907         Bladder cancer
22  2009       947         Bladder cancer
23  2010      1054         Bladder cancer
24  2011      1136         Bladder cancer
25  2012      1324         Bladder cancer
27  2013      1525         Bladder cancer
28  2014      1720         Bladder cancer
30  2015      1725         Bladder cancer
31  2016      1852         Bladder cancer
32  2017      1810         Bladder cancer
33  2018      2074         Bladder cancer
35  2019      2229         Bladder cancer
34  2020      2481         Bladder cancer
37  2021      2935         Bladder cancer
38  2022      2943         Bladder cancer
39  2023      2774         Bladder cancer
41  2024      2022         Bladder cancer
36  2025        42         Bladder cancer
41  1984       286           Brain cancer
27  1985       778           Brain cancer
7   1986       789           Brain cancer
28  1987       835           Brain cancer
13  1988       826           Brain cancer
12  1989       962           Brain cancer
1   1990       954           Brain cancer
2   1991       895           Brain cancer
0   1992      1036           Brain cancer
24  1993      1106           Brain cancer
8   1994      1271           Brain cancer
9   1995      

In [290]:
# Save
df_year_cancer_agg.to_csv(DF_prepared_output + "articles_year_cancer.csv", index=False)

### 2.4.- Aggregate number of articles per cancer per country

Here, a csv is generated in which, for each country, the number of studies per cancer, in all years combined, is calculated. 

In [155]:
# Create and structure dict to hold data about publications on each cancer type
cancer_country_aggregates = {}

for country in set(df_globocan_lite["Country"]):
    cancer_country_aggregates[country] = {}

    for cancer in cancer_names:
        cancer_country_aggregates[country][cancer] = 0

# Parse all articles' csv and count the number of studies per cancer and country
for csv in tqdm(list_csvs_match_GLOBOCAN):
    df = pd.read_csv(DF_input + csv)
    for row in df.index:
        for cancer in cancer_names:
            country = df.at[row, "Country"]
            if pd.notna(country) and df.at[row, cancer] > 0:
                cancer_country_aggregates[country][cancer] += 1

    del df, cancer, country, csv

cancer_country_aggregates

100%|█████████████████████████| 45/45 [22:24<00:00, 29.89s/it]


{'Brunei Darussalam': {'Anal cancer': 0,
  'Bladder cancer': 0,
  'Brain cancer': 2,
  'Breast cancer': 11,
  'Cervical cancer': 7,
  'Colon cancer': 2,
  'Colorectal cancer': 16,
  'Esophageal cancer': 1,
  'Gallbladder cancer': 0,
  'Hodgkin lymphoma': 1,
  'Kaposi sarcoma': 0,
  'Kidney cancer': 1,
  'Laryngeal cancer': 0,
  'Leukemia': 3,
  'Liver cancer': 2,
  'Lung cancer': 3,
  'Mesothelioma': 1,
  'Mouth cancer': 0,
  'Multiple myeloma': 2,
  'Non-Hodgkin lymphoma': 1,
  'Other cancer': 19,
  'Ovarian cancer': 1,
  'Pancreatic cancer': 0,
  'Penile cancer': 0,
  'Prostate cancer': 2,
  'Rectal cancer': 2,
  'Salivary gland cancer': 0,
  'Skin cancer': 1,
  'Stomach cancer': 1,
  'Testicular cancer': 0,
  'Throat cancer': 0,
  'Thyroid cancer': 0,
  'Undetermined_Cancer': 63,
  'Uterine cancer': 0,
  'Vaginal cancer': 0,
  'Vulvar cancer': 0},
 'Slovakia': {'Anal cancer': 0,
  'Bladder cancer': 21,
  'Brain cancer': 78,
  'Breast cancer': 309,
  'Cervical cancer': 48,
  'Colon c

In [156]:
# Create df from dict
dfs_cancer_country = []
for country in cancer_country_aggregates.keys():
    df = pd.DataFrame.from_dict(cancer_country_aggregates[country], orient="index", columns = ["Articles"])
    df.reset_index(inplace=True)
    df.rename(columns={"index": "Cancer"}, inplace=True)
    df["Country"] = country
    dfs_cancer_country.append(df)

df_cancer_country_agg = pd.concat(dfs_cancer_country)

In [157]:
df_cancer_country_agg

Cancer  Articles                   Country
0             Anal cancer         0         Brunei Darussalam
1          Bladder cancer         0         Brunei Darussalam
2            Brain cancer         2         Brunei Darussalam
3           Breast cancer        11         Brunei Darussalam
4         Cervical cancer         7         Brunei Darussalam
5            Colon cancer         2         Brunei Darussalam
6       Colorectal cancer        16         Brunei Darussalam
7       Esophageal cancer         1         Brunei Darussalam
8      Gallbladder cancer         0         Brunei Darussalam
9        Hodgkin lymphoma         1         Brunei Darussalam
10         Kaposi sarcoma         0         Brunei Darussalam
11          Kidney cancer         1         Brunei Darussalam
12       Laryngeal cancer         0         Brunei Darussalam
13               Leukemia         3         Brunei Darussalam
14           Liver cancer         2         Brunei Darussalam
15            Lung cancer         3         Brunei Darussalam
16           Mesothelioma         1         Brunei Darussalam
17           Mouth cancer         0         Brunei Darussalam
18       Multiple myeloma         2         Brunei Darussalam
19   Non-Hodgkin lymphoma         1         Brunei Darussalam
20           Other cancer        19         Brunei Darussalam
21         Ovarian cancer         1         Brunei Darussalam
22      Pancreatic cancer         0         Brunei Darussalam
23          Penile cancer         0         Brunei Darussalam
24        Prostate cancer         2         Brunei Darussalam
25          Rectal cancer         2         Brunei Darussalam
26  Salivary gland cancer         0         Brunei Darussalam
27            Skin cancer         1         Brunei Darussalam
28         Stomach cancer         1         Brunei Darussalam
29      Testicular cancer         0         Brunei Darussalam
30          Throat cancer         0         Brunei Darussalam
31         Thyroid cancer         0         Brunei Darussalam
32    Undetermined_Cancer        63         Brunei Darussalam
33         Uterine cancer         0         Brunei Darussalam
34         Vaginal cancer         0         Brunei Darussalam
35          Vulvar cancer         0         Brunei Darussalam
0             Anal cancer         0                  Slovakia
1          Bladder cancer        21                  Slovakia
2            Brain cancer        78                  Slovakia
3           Breast cancer       309                  Slovakia
4         Cervical cancer        48                  Slovakia
5            Colon cancer        50                  Slovakia
6       Colorectal cancer       148                  Slovakia
7       Esophageal cancer         6                  Slovakia
8      Gallbladder cancer         4                  Slovakia
9        Hodgkin lymphoma        13                  Slovakia
10         Kaposi sarcoma         3                  Slovakia
11          Kidney cancer        34                  Slovakia
12       Laryngeal cancer         1                  Slovakia
13               Leukemia       366                  Slovakia
14           Liver cancer        20                  Slovakia
15            Lung cancer        37                  Slovakia
16           Mesothelioma         4                  Slovakia
17           Mouth cancer         0                  Slovakia
18       Multiple myeloma        31                  Slovakia
19   Non-Hodgkin lymphoma        14                  Slovakia
20           Other cancer       479                  Slovakia
21         Ovarian cancer        48                  Slovakia
22      Pancreatic cancer        15                  Slovakia
23          Penile cancer         0                  Slovakia
24        Prostate cancer        99                  Slovakia
25          Rectal cancer        10                  Slovakia
26  Salivary gland cancer         0                  Slovakia
27            Skin cancer       161                

In [158]:
# Save
df_cancer_country_agg.to_csv(DF_prepared_output + "articles_cancer_country.csv", index=False)

### 2.5.- Most studied cancer per country

By using the aggregated data from the last dataframe, a new dataframe is obtained containing a column with the most studied cancer in each country. Here the categories **Other cancer** and **Undetermined_cancer** are not taken into consideration

In [280]:
df_articles_filtered = df_cancer_country_agg.loc[~df_cancer_country_agg["Cancer"].isin(["Other cancer", "Undetermined_Cancer"])]

In [278]:
list_most_studied_cancer = []

for country in set(df_globocan_lite["Country"]):
    df = df_articles_filtered.loc[df_articles_filtered["Country"] == country]
    list_most_studied_cancer.append(df.sort_values(by="Articles", ascending=False)[:1])

df_max_studied_cancer = pd.concat(list_most_studied_cancer).sort_values(by="Country")
df_max_studied_cancer

Cancer  Articles                   Country
3       Breast cancer        13               Afghanistan
3       Breast cancer         5                   Albania
3       Breast cancer        53                   Algeria
18   Multiple myeloma         3                    Angola
3       Breast cancer       793                 Argentina
13           Leukemia        15                   Armenia
3       Breast cancer      6444                 Australia
3       Breast cancer      1808                   Austria
3       Breast cancer        10                Azerbaijan
3       Breast cancer         8                   Bahamas
3       Breast cancer        50                   Bahrain
3       Breast cancer       136                Bangladesh
5        Colon cancer         5                  Barbados
13           Leukemia        45                   Belarus
3       Breast cancer      2676                   Belgium
4     Cervical cancer         2                    Belize
3       Breast cancer        32                     Benin
4     Cervical cancer         6                    Bhutan
13           Leukemia         3                   Bolivia
3       Breast cancer        80    Bosnia and Herzegovina
4     Cervical cancer        39                  Botswana
3       Breast cancer      3313                    Brazil
6   Colorectal cancer        16         Brunei Darussalam
3       Breast cancer       173                  Bulgaria
4     Cervical cancer        18              Burkina Faso
3       Breast cancer         2                   Burundi
0         Anal cancer         0                Cabo Verde
4     Cervical cancer         8                  Cambodia
3       Breast cancer        39                  Cameroon
3       Breast cancer     10565                    Canada
15        Lung cancer         2  Central African Republic
6   Colorectal cancer         1                      Chad
3       Breast cancer       372                     Chile
15        Lung cancer     69390                     China
3       Breast cancer       289                  Colombia
3       Breast cancer        11                   Comoros
3       Breast cancer        10            Congo Republic
13           Leukemia        26                Costa Rica
4     Cervical cancer        13             Cote d'Ivoire
3       Breast cancer       365                   Croatia
27        Skin cancer        52                      Cuba
3       Breast cancer       145                    Cyprus
13           Leukemia      1173                   Czechia
4     Cervical cancer        10                  DR Congo
3       Breast cancer      2714                   Denmark
7   Esophageal cancer         1                  Djibouti
3       Breast cancer         3        Dominican Republic
3       Breast cancer        23                   Ecuador
3       Breast cancer      1848                     Egypt
13           Leukemia        19               El Salvador
21     Ovarian cancer        14                   Eritrea
3       Breast cancer        49                   Estonia
3       Breast cancer         8                  Eswatini
4     Cervical cancer       277                  Ethiopia
3       Breast cancer         2                      Fiji
3       Breast cancer      1879                   Finland
3       Breast cancer     10024                    France
13           Leukemia         7             French Guiana
13           Leukemia         2          French Polynesia
2        Brain cancer        10                     Gabon
15        Lung cancer        20                    Gambia
3       Breast cancer        10                   Georgia
13           Leukemia     11294                   Germany
3       Breast cancer       149                     Ghana
3       Breast cancer      2285                    Greece
24    Prostate cancer        20                Guadeloupe
13           Leukemia         5                      Guam
4     Cervical cancer         8                 Guatemala
3       Breas

In [282]:
# Save
df_max_studied_cancer.to_csv(DF_prepared_output + "articles_cancer_most_studied_country.csv", index = False)

### 2.6.- Number of cancer studies per country and cancer type

Here, a csv is generated in which, for each country and cancer type, the number of studies per year is calculated.

In [323]:
# Create and structure dict to hold data about publications on each cancer type
country_year_cancer_aggregates = {}

for country in set(df_globocan_lite["Country"]):
    country_year_cancer_aggregates[country] = {}
    for cancer in cancer_names:
        country_year_cancer_aggregates[country][cancer] = {}

for csv in tqdm(list_csvs_match_GLOBOCAN):
    df = pd.read_csv(DF_input + csv)
    for country in set(df["Country"]):
        if pd.notna(country):
            df_country = df.loc[df["Country"] == country]
            for cancer in cancer_names:
                df_country_cancer = df_country.loc[df_country[cancer] > 0]
                for year in set(df_country_cancer["PublicationDate"]):
                    if pd.notna(year):
                        if int(year) in country_year_cancer_aggregates[country][cancer].keys():
                            country_year_cancer_aggregates[country][cancer][int(year)] += len(df_country_cancer.loc[df_country_cancer["PublicationDate"] == year])
                        else:
                            country_year_cancer_aggregates[country][cancer][int(year)] = len(df_country_cancer.loc[df_country_cancer["PublicationDate"] == year])
                        
country_year_cancer_aggregates  

100%|█████████████████████████| 45/45 [05:03<00:00,  6.75s/it]


{'Brunei Darussalam': {'Anal cancer': {},
  'Bladder cancer': {},
  'Brain cancer': {2022: 1, 2023: 1},
  'Breast cancer': {2011: 1, 2017: 1, 2020: 1, 2023: 5, 2022: 1, 2024: 2},
  'Cervical cancer': {2012: 1, 2019: 1, 2022: 1, 2023: 2, 1994: 1, 1993: 1},
  'Colon cancer': {2015: 1, 2022: 1},
  'Colorectal cancer': {2009: 1,
   2011: 1,
   2013: 1,
   2015: 3,
   2016: 1,
   2019: 1,
   2020: 3,
   2021: 1,
   2022: 3,
   2023: 1},
  'Esophageal cancer': {2015: 1},
  'Gallbladder cancer': {},
  'Hodgkin lymphoma': {2023: 1},
  'Kaposi sarcoma': {},
  'Kidney cancer': {2022: 1},
  'Laryngeal cancer': {},
  'Leukemia': {2002: 1, 2016: 1, 2020: 1},
  'Liver cancer': {2009: 1, 2013: 1},
  'Lung cancer': {2009: 1, 2013: 1, 2022: 1},
  'Mesothelioma': {2021: 1},
  'Mouth cancer': {},
  'Multiple myeloma': {2021: 2},
  'Non-Hodgkin lymphoma': {2023: 1},
  'Other cancer': {2008: 1,
   2009: 2,
   2013: 1,
   2014: 2,
   2015: 3,
   2016: 2,
   2020: 1,
   2021: 2,
   2023: 3,
   2024: 1,
   19

In [331]:
# Assign value 0 to any country, cancer, year combination without a value in the aggregates (e.g. without any published article)
years_articles_dataset = []

for country in country_year_cancer_aggregates.keys():
    for cancer in cancer_names:
        years_articles_dataset += list(country_year_cancer_aggregates[country][cancer].keys())

years_articles_dataset = set(years_articles_dataset)

for year in years_articles_dataset:
    for country in country_year_cancer_aggregates.keys():
        for cancer in country_year_cancer_aggregates[country].keys():
            if year not in country_year_cancer_aggregates[country][cancer].keys():
                country_year_cancer_aggregates[country][cancer][year] = 0

In [337]:
# Create df from dict
dfs_contry_year_cancer = []
for country in country_year_cancer_aggregates.keys():
    for cancer in country_year_cancer_aggregates[country].keys():
        df = pd.DataFrame.from_dict(country_year_cancer_aggregates[country][cancer], orient="index", columns = ["Articles"])
        df.reset_index(inplace=True)
        df.rename(columns={"index": "Year"}, inplace=True)
        df["Country"] = country
        df["Cancer"] = cancer
        dfs_contry_year_cancer.append(df)

        del df

df_country_year_cancer_agg = pd.concat(dfs_contry_year_cancer)

In [338]:
df_country_year_cancer_agg

Year  Articles            Country         Cancer
0   1984         0  Brunei Darussalam    Anal cancer
1   1985         0  Brunei Darussalam    Anal cancer
2   1986         0  Brunei Darussalam    Anal cancer
3   1987         0  Brunei Darussalam    Anal cancer
4   1988         0  Brunei Darussalam    Anal cancer
..   ...       ...                ...            ...
37  2021         0            Lesotho  Vulvar cancer
38  2022         0            Lesotho  Vulvar cancer
39  2023         0            Lesotho  Vulvar cancer
40  2024         0            Lesotho  Vulvar cancer
41  2025         0            Lesotho  Vulvar cancer

[279720 rows x 4 columns]

In [342]:
df_country_year_cancer_agg.to_csv(DF_prepared_output + "articles_country_year_cancer.csv", index = False)